##### 포즈 landmarks 좌표 소켓 서버 전송

In [7]:
import mediapipe as mp
import cv2
import socket

# TCP 서버 설정
def send_pose_landmarks(host='192.168.239.210', port=6521):
    # 소켓 객체 생성
    with socket.socket(socket.AF_INET, socket.SOCK_STREAM) as client_socket:
        # 서버에 연결
        client_socket.connect((host, port))
        print(f"서버에 연결되었습니다. {host}:{port}")

        # MediaPipe Pose 설정
        pose = mp.solutions.pose.Pose(
            static_image_mode=False,
            model_complexity=1,
            smooth_landmarks=True,
            enable_segmentation=False,  # 세그멘테이션 기능 비활성화
            min_detection_confidence=0.5,
            min_tracking_confidence=0.5)

        # 그리기 함수 초기화
        mp_drawing = mp.solutions.drawing_utils

        # 웹캠 캡처
        cap = cv2.VideoCapture(0)

        while True:
            # 이미지 읽기
            ret, image = cap.read()
            if not ret:
                break

            # 이미지 변환
            image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)

            # 포즈 추정
            results = pose.process(image)

            # 추정된 포즈 정보 확인
            if results.pose_landmarks:
                # 포즈 랜드마크를 리스트로 변환하여 문자열로 만듦
                pose_landmarks_str = ';'.join(
                    [f"{lm.x},{lm.y},{lm.z}" for lm in results.pose_landmarks.landmark])

                # 포즈 랜드마크 문자열 출력
                print(pose_landmarks_str)

                # 포즈 랜드마크 문자열을 서버로 전송
                client_socket.sendall(pose_landmarks_str.encode())

            # 이미지 출력
            image = cv2.cvtColor(image, cv2.COLOR_RGB2BGR)
            mp_drawing.draw_landmarks(
                image, results.pose_landmarks, mp.solutions.pose.POSE_CONNECTIONS)
            cv2.imshow('MediaPipe Pose', image)

            # 키 입력 처리
            if cv2.waitKey(5) & 0xFF == ord('q'):
                break

        # 자원 해제
        cap.release()
        cv2.destroyAllWindows()

if __name__ == "__main__":
    send_pose_landmarks()

서버에 연결되었습니다. 192.168.239.210:6521
0.7556825876235962,0.685994565486908,-1.1652398109436035;0.7620863914489746,0.6267766952514648,-1.0694104433059692;0.7762311100959778,0.6249868869781494,-1.0696256160736084;0.789684534072876,0.6236298084259033,-1.069888949394226;0.7114487886428833,0.639801561832428,-1.1107873916625977;0.6888109445571899,0.6486524343490601,-1.110547423362732;0.6659658551216125,0.6580089330673218,-1.1112765073776245;0.7869763374328613,0.6679620742797852,-0.5286969542503357;0.6173514127731323,0.7082043886184692,-0.6959961652755737;0.7819784879684448,0.7643623352050781,-0.9655581712722778;0.7239580154418945,0.7779397964477539,-1.01339590549469;0.9097363352775574,1.0265008211135864,-0.18535980582237244;0.4899713397026062,1.0336410999298096,-0.5832540392875671;1.0428000688552856,1.3847806453704834,-0.11654212325811386;0.40529680252075195,1.5124256610870361,-0.7387577891349792;1.016952633857727,1.5834407806396484,-0.48433488607406616;0.536650538444519,1.7649494409561157,-1.29

: 